In [ ]:
# jetbot_control.py (JetBot - WebSocket Server + JetBot Control + Webcam Streaming)

import asyncio
import websockets
import json
import logging
from jetbot import Robot
import subprocess  # mjpg-streamer
from aiohttp import web
import aiohttp_cors

# --- 로깅 ---
logging.basicConfig(level=logging.DEBUG)
logger = logging.getLogger(__name__)

# --- 설정 ---
WEBSOCKET_PORT = 8765

# --- JetBot ---
robot = Robot()

# --- TTS 관련 코드 제거 ---

# --- JetBot 명령 처리 ---
async def handle_command(command: str, parameters: dict = None):
    logger.info(f"Handling JetBot command: {command}, Parameters: {parameters}")

    if command == "move_forward":
        robot.forward(0.4)
        await asyncio.sleep(1)
        robot.stop()
    elif command == "move_backward":
        robot.backward(0.4)
        await asyncio.sleep(1)
        robot.stop()
    elif command == "turn_left":
        robot.left(0.3)
        await asyncio.sleep(0.7)
        robot.stop()
    elif command == "turn_right":
        robot.right(0.3)
        await asyncio.sleep(0.7)
        robot.stop()
    elif command == "avoid_obstacle":
        if parameters and "direction" in parameters:
            direction = parameters["direction"]
            if direction == "left":
                robot.left(0.5)
                await asyncio.sleep(1.2)
            elif direction == "right":
                robot.right(0.5)
                await asyncio.sleep(1.2)
        else: # 기본값
            robot.left(0.5)
            await asyncio.sleep(1.2)

        robot.forward(0.4)
        await asyncio.sleep(1)
        robot.stop()

    elif command == "none":
        pass  # No action
    else:
        logger.warning(f"Unknown command: {command}")


# --- 웹소켓 서버 ---
async def websocket_handler(websocket, path):
    logger.info(f"New WebSocket connection: {websocket.remote_address}")
    try:
        async for message in websocket:
            try:
                data = json.loads(message)
                logger.debug(f"Received message: {data}")
                if "command" in data:
                    await handle_command(data["command"], data.get("parameters"))
                else:
                    logger.warning("Invalid message format")
            except json.JSONDecodeError as e:
                logger.error(f"JSON decode error: {e}")
            except Exception as e:
                logger.exception(f"Error handling command: {e}")
    except websockets.exceptions.ConnectionClosedOK:
        logger.info("WebSocket connection closed")
    except Exception as e:
        logger.exception(f"WebSocket error: {e}")

async def start_websocket_server():
    server = await websockets.serve(websocket_handler, "0.0.0.0", WEBSOCKET_PORT)
    logger.info(f"WebSocket server started (port: {WEBSOCKET_PORT})")
    await server.wait_closed()

# --- 웹캠 스트리밍 (mjpeg-streamer) ---
async def start_mjpeg_streamer():
    command = [
        "mjpg_streamer",
        "-i", "input_uvc.so -r 640x480 -f 10 -d /dev/video0",  # 해상도, 프레임, 장치 조정
        "-o", "output_http.so -w /usr/share/mjpg-streamer/www -p 8080"
    ]

    try:
        process = await asyncio.create_subprocess_exec(*command)
        logger.info(f"mjpg-streamer started (PID: {process.pid})")
    except Exception as e:
        logger.error(f"Error starting mjpg-streamer: {e}")

# --- aiohttp 웹 서버 (웹캠 스트리밍 제공) ---
async def webcam_handler(request):
    return web.Response(
        text='<html><body><img src="http://127.0.0.1:8080/?action=stream"></body></html>',
        content_type='text/html'
    )

async def index_handler(request): # index
    return web.FileResponse('./static/index.html')

async def create_aiohttp_app():
    app = web.Application()

    # CORS 설정
    cors = aiohttp_cors.setup(app, defaults={
        "*": aiohttp_cors.ResourceOptions(
            allow_credentials=True,
            expose_headers="*",
            allow_headers="*",
        )
    })

    app.router.add_get('/webcam', webcam_handler)
    app.router.add_get('/', index_handler)  # index
    app.router.add_static('/static/', path='static', name='static') # index

    for route in list(app.router.routes()):
        cors.add(route)

    return app

async def main():
    websocket_task = asyncio.create_task(start_websocket_server())
    mjpeg_streamer_task = asyncio.create_task(start_mjpeg_streamer())

    aiohttp_app = await create_aiohttp_app()
    runner = web.AppRunner(aiohttp_app)
    await runner.setup()
    site = web.TCPSite(runner, '0.0.0.0', 8000)  # 8000번 포트 사용
    await site.start()

    await asyncio.gather(websocket_task, mjpeg_streamer_task)

if __name__ == "__main__":
    asyncio.run(main())

In [2]:
!pip install websockets aiohttp aiohttp_cors
!sudo apt-get update
!sudo apt-get install -y libsndfile1  # edge-tts (PC에서 사용하지만, 종속성은 JetBot에도 설치)
!sudo apt-get install -y mjpg-streamer v4l-utils

/bin/bash: pip: command not found
/bin/bash: sudo: command not found


UnboundLocalError: local variable 'child' referenced before assignment

In [3]:
import sys
!{sys.executable} -m pip install websockets aiohttp aiohttp_cors

    100% |################################| 81kB 3.0MB/s ta 0:00:011
    100% |################################| 7.4MB 66kB/s  eta 0:00:01    99% |############################### | 7.3MB 20.2MB/s eta 0:00:01
    100% |################################| 51kB 3.8MB/s eta 0:00:01
    100% |################################| 51kB 2.9MB/s eta 0:00:01
    100% |################################| 174kB 2.4MB/s eta 0:00:01
    100% |################################| 71kB 3.9MB/s eta 0:00:01
  Running setup.py bdist_wheel for websockets ... done
  Stored in directory: /root/.cache/pip/wheels/e1/f7/3f/bb9bd14321f58f036e48804fb6bfe2cfd431c41d8306c801f4
  Running setup.py bdist_wheel for aiohttp ... done
  Stored in directory: /root/.cache/pip/wheels/a3/d1/b5/d2eaa71fe3f86b7491e65f2b98cccec9052e01072a0b049354
  Running setup.py bdist_wheel for multidict ... done
  Stored in directory: /root/.cache/pip/wheels/73/7f/38/4d6e62cf67f06a8bb2a69464ee8d7611da2236fd83ce1b33de
  Running setup.py bdist_wheel fo

In [4]:
# jetbot_control.py (JetBot - WebSocket Server + JetBot Control + Webcam Streaming)

import asyncio
import websockets
import json
import logging
from jetbot import Robot
import subprocess
from aiohttp import web
import aiohttp_cors

# --- 로깅 ---
logging.basicConfig(level=logging.DEBUG)
logger = logging.getLogger(__name__)

# --- 설정 ---
WEBSOCKET_PORT = 8765

# --- JetBot ---
robot = Robot()

# --- JetBot 명령 처리 ---
async def handle_command(command: str, parameters: dict = None):
    logger.info(f"Handling JetBot command: {command}, Parameters: {parameters}")

    if command == "move_forward":
        robot.forward(0.4)
        await asyncio.sleep(1)
        robot.stop()
    elif command == "move_backward":
        robot.backward(0.4)
        await asyncio.sleep(1)
        robot.stop()
    elif command == "turn_left":
        robot.left(0.3)
        await asyncio.sleep(0.7)
        robot.stop()
    elif command == "turn_right":
        robot.right(0.3)
        await asyncio.sleep(0.7)
        robot.stop()
    elif command == "avoid_obstacle":
        if parameters and "direction" in parameters:
            direction = parameters["direction"]
            if direction == "left":
                robot.left(0.5)
                await asyncio.sleep(1.2)
            elif direction == "right":
                robot.right(0.5)
                await asyncio.sleep(1.2)
        else:
            robot.left(0.5)
            await asyncio.sleep(1.2)

        robot.forward(0.4)
        await asyncio.sleep(1)
        robot.stop()

    elif command == "none":
        pass
    else:
        logger.warning(f"Unknown command: {command}")

# --- 웹소켓 서버 ---
async def websocket_handler(websocket, path):
    logger.info(f"New WebSocket connection: {websocket.remote_address}")
    try:
        async for message in websocket:
            try:
                data = json.loads(message)
                logger.debug(f"Received message: {data}")
                if "command" in data:
                    await handle_command(data["command"], data.get("parameters"))
                else:
                    logger.warning("Invalid message format")
            except json.JSONDecodeError as e:
                logger.error(f"JSON decode error: {e}")
            except Exception as e:
                logger.exception(f"Error handling command: {e}")
    except websockets.exceptions.ConnectionClosedOK:
        logger.info("WebSocket connection closed")
    except Exception as e:
        logger.exception(f"WebSocket error: {e}")

async def start_websocket_server():
    server = await websockets.serve(websocket_handler, "0.0.0.0", WEBSOCKET_PORT)
    logger.info(f"WebSocket server started (port: {WEBSOCKET_PORT})")
    await server.wait_closed()

# --- 웹캠 스트리밍 (mjpg-streamer) ---
async def start_mjpeg_streamer():
    command = [
        "mjpg_streamer",
        "-i", "input_uvc.so -r 640x480 -f 10 -d /dev/video0",
        "-o", "output_http.so -w /usr/share/mjpg-streamer/www -p 8080"
    ]
    try:
        process = await asyncio.create_subprocess_exec(*command)
        logger.info(f"mjpg-streamer started (PID: {process.pid})")
    except Exception as e:
        logger.error(f"Error starting mjpg-streamer: {e}")

# --- aiohttp 웹 서버 (웹캠 스트리밍) ---
async def webcam_handler(request):
    return web.Response(
        text='<html><body><img src="http://127.0.0.1:8080/?action=stream"></body></html>',
        content_type='text/html'
    )

async def create_aiohttp_app():
    app = web.Application()

    # CORS 설정
    cors = aiohttp_cors.setup(app, defaults={
        "*": aiohttp_cors.ResourceOptions(
            allow_credentials=True,
            expose_headers="*",
            allow_headers="*",
        )
    })

    # 경로 설정
    app.router.add_get('/webcam', webcam_handler)
    # index.html 관련 라우트 제거!

    # CORS 적용
    for route in list(app.router.routes()):
        cors.add(route)

    return app

async def main():
    websocket_task = asyncio.create_task(start_websocket_server())
    mjpeg_streamer_task = asyncio.create_task(start_mjpeg_streamer())

    aiohttp_app = await create_aiohttp_app()
    runner = web.AppRunner(aiohttp_app)
    await runner.setup()
    site = web.TCPSite(runner, '0.0.0.0', 8000)
    await site.start()

    await asyncio.gather(websocket_task, mjpeg_streamer_task)

if __name__ == "__main__":
    asyncio.run(main())

TypeError: 'ABCMeta' object is not subscriptable

In [5]:
import sys
!{sys.executable} -m pip show fastapi uvicorn httpx websockets pydantic python-multipart edge-tts

Name: websockets
Version: 9.1
Summary: An implementation of the WebSocket Protocol (RFC 6455 & 7692)
Home-page: https://github.com/aaugustin/websockets
Author: Aymeric Augustin
Author-email: aymeric.augustin@m4x.org
License: BSD
Location: /usr/local/lib/python3.6/dist-packages
Requires: 


In [6]:
import sys
!{sys.executable} -m pip show websockets aiohttp aiohttp-cors
!{sys.executable} -m pip show jetbot # jetbot 버전도 확인

Name: websockets
Version: 9.1
Summary: An implementation of the WebSocket Protocol (RFC 6455 & 7692)
Home-page: https://github.com/aaugustin/websockets
Author: Aymeric Augustin
Author-email: aymeric.augustin@m4x.org
License: BSD
Location: /usr/local/lib/python3.6/dist-packages
Requires: 
---
Name: aiohttp
Version: 3.8.6
Summary: Async http client/server framework (asyncio)
Home-page: https://github.com/aio-libs/aiohttp
Author: None
Author-email: None
License: Apache 2
Location: /usr/local/lib/python3.6/dist-packages
Requires: idna-ssl, yarl, multidict, charset-normalizer, frozenlist, async-timeout, aiosignal, attrs, asynctest, typing-extensions
---
Name: aiohttp-cors
Version: 0.8.0
Summary: CORS support for aiohttp
Home-page: https://github.com/aio-libs/aiohttp-cors
Author: Vladimir Rutsky and aio-libs team
Author-email: vladimir@rutsky.org
License: Apache License, Version 2.0
Location: /usr/local/lib/python3.6/dist-packages
Requires: aiohttp


UnboundLocalError: local variable 'child' referenced before assignment

In [13]:
# jetbot_control.py (JetBot - WebSocket Server + JetBot Control + Webcam Streaming)

import asyncio
import websockets
import json
import logging
from jetbot import Robot
import subprocess
from aiohttp import web
# import aiohttp_cors  # 제거

# --- 로깅 ---
logging.basicConfig(level=logging.DEBUG)
logger = logging.getLogger(__name__)

# --- 설정 ---
WEBSOCKET_PORT = 8765
AIOHTTP_PORT = 8001  # aiohttp 포트 변경 (8000 -> 8001)

# --- JetBot ---
robot = Robot()

# --- JetBot 명령 처리 ---
async def handle_command(command: str, parameters: dict = None):
    logger.info(f"Handling JetBot command: {command}, Parameters: {parameters}")

    if command == "move_forward":
        robot.forward(0.4)
        await asyncio.sleep(1)
        robot.stop()
    elif command == "move_backward":
        robot.backward(0.4)
        await asyncio.sleep(1)
        robot.stop()
    elif command == "turn_left":
        robot.left(0.3)
        await asyncio.sleep(0.7)
        robot.stop()
    elif command == "turn_right":
        robot.right(0.3)
        await asyncio.sleep(0.7)
        robot.stop()
    elif command == "avoid_obstacle":
        if parameters and "direction" in parameters:
            direction = parameters["direction"]
            if direction == "left":
                robot.left(0.5)
                await asyncio.sleep(1.2)
            elif direction == "right":
                robot.right(0.5)
                await asyncio.sleep(1.2)
        else:
            robot.left(0.5)
            await asyncio.sleep(1.2)

        robot.forward(0.4)
        await asyncio.sleep(1)
        robot.stop()

    elif command == "none":
        pass
    else:
        logger.warning(f"Unknown command: {command}")

# --- 웹소켓 서버 (websockets 9.1 호환) ---
async def websocket_handler(websocket, path):
    logger.info(f"New WebSocket connection: {websocket.remote_address}")
    try:
        async for message in websocket:
            try:
                data = json.loads(message)
                logger.debug(f"Received message: {data}")
                if "command" in data:
                    await handle_command(data["command"], data.get("parameters"))
                else:
                    logger.warning("Invalid message format")
            except json.JSONDecodeError as e:
                logger.error(f"JSON decode error: {e}")
            except Exception as e:
                logger.exception(f"Error handling command: {e}")
    except websockets.exceptions.ConnectionClosedOK:
        logger.info("WebSocket connection closed")
    except Exception as e:
        logger.exception(f"WebSocket error: {e}")

async def start_websocket_server():
    server = await websockets.serve(websocket_handler, "0.0.0.0", WEBSOCKET_PORT)
    logger.info(f"WebSocket server started (port: {WEBSOCKET_PORT})")
    await server.wait_closed()

# --- 웹캠 스트리밍 (mjpg-streamer) ---
async def start_mjpeg_streamer():
    command = [
        "mjpg_streamer",
        "-i", "input_uvc.so -r 640x480 -f 10 -d /dev/video0",
        "-o", "output_http.so -w /usr/share/mjpg-streamer/www -p 8080"
    ]
    try:
        process = await asyncio.create_subprocess_exec(*command)
        logger.info(f"mjpg-streamer started (PID: {process.pid})")
    except Exception as e:
        logger.error(f"Error starting mjpg-streamer: {e}")
        print(f"mjpg-streamer 실행 중 오류 발생: {e}")
        print("mjpg-streamer가 설치되어 있고, /dev/video0 장치가 올바른지 확인하세요.")

# --- aiohttp 웹 서버 (웹캠 스트리밍, CORS 직접 처리) ---
async def webcam_handler(request):
    response = web.Response(
        text='<html><body><img src="http://127.0.0.1:8080/?action=stream"></body></html>',
        content_type='text/html'
    )
    # CORS 헤더 추가
    response.headers['Access-Control-Allow-Origin'] = '*'
    response.headers['Access-Control-Allow-Methods'] = 'GET, POST, OPTIONS'
    response.headers['Access-Control-Allow-Headers'] = 'Content-Type'
    return response

async def create_aiohttp_app():
    app = web.Application()

    # 경로 설정
    app.router.add_get('/webcam', webcam_handler)

    return app

async def main():
    # aiohttp 웹 서버 시작 (별도 태스크)
    aiohttp_app = await create_aiohttp_app()
    runner = web.AppRunner(aiohttp_app)
    await runner.setup()
    site = web.TCPSite(runner, '0.0.0.0', AIOHTTP_PORT)  # 변경된 포트 사용
    await site.start()

    # 웹소켓 서버 시작 (별도 태스크)
    websocket_task = asyncio.ensure_future(start_websocket_server())

    # mjpg-streamer 시작 (별도 태스크)
    mjpeg_streamer_task = asyncio.ensure_future(start_mjpeg_streamer())

    await websocket_task

if __name__ == "__main__":
    asyncio.ensure_future(main())

DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Reseting PCA9685 MODE1 (without SLEEP) and MODE2
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFA
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFB
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFC
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFD
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x04 to register 0x01
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x01 to register 0x00
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Read 0x01 from register 0x00
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x01 to register 0x00
DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Setting PWM frequency to 1600 Hz
DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Estimated pre-scale: 2
DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Final pre-scale: 3
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Read 0x01 from register 0x00
DEBUG:Adafruit_I2

mjpg-streamer 실행 중 오류 발생: [Errno 2] No such file or directory: 'mjpg_streamer': 'mjpg_streamer'
mjpg-streamer가 설치되어 있고, /dev/video0 장치가 올바른지 확인하세요.


In [1]:
# jetbot_control.py (JetBot - WebSocket Server + JetBot Control + Image Send)

import asyncio
import websockets
import json
import logging
from jetbot import Robot, Camera, bgr8_to_jpeg
import base64
import time

# --- 로깅 ---
logging.basicConfig(level=logging.DEBUG)
logger = logging.getLogger(__name__)

# --- 설정 ---
WEBSOCKET_PORT = 8766  # 웹소켓 포트 변경 (8765 -> 8766)
CAMERA_WIDTH = 300
CAMERA_HEIGHT = 300

# --- JetBot ---
robot = Robot()
camera = Camera.instance(width=CAMERA_WIDTH, height=CAMERA_HEIGHT)

# --- JetBot 명령 처리 ---
async def handle_command(command: str, parameters: dict = None):
    logger.info(f"Handling JetBot command: {command}, Parameters: {parameters}")
    if command == "move_forward":
        robot.forward(0.4)
        await asyncio.sleep(1)
        robot.stop()
    elif command == "move_backward":
        robot.backward(0.4)
        await asyncio.sleep(1)
        robot.stop()
    elif command == "turn_left":
        robot.left(0.3)
        await asyncio.sleep(0.7)
        robot.stop()
    elif command == "turn_right":
        robot.right(0.3)
        await asyncio.sleep(0.7)
        robot.stop()
    elif command == "avoid_obstacle":
        if parameters and "direction" in parameters:
            direction = parameters["direction"]
            if direction == "left":
                robot.left(0.5)
                await asyncio.sleep(1.2)
            elif direction == "right":
                robot.right(0.5)
                await asyncio.sleep(1.2)
        else:
            robot.left(0.5)
            await asyncio.sleep(1.2)

        robot.forward(0.4)
        await asyncio.sleep(1)
        robot.stop()
    elif command == "none":
        pass
    else:
        logger.warning(f"Unknown command: {command}")

# --- 웹소켓 서버 ---
async def websocket_handler(websocket, path):
    logger.info(f"New WebSocket connection: {websocket.remote_address}")
    try:
        # 이미지 전송 태스크 시작
        image_task = asyncio.ensure_future(send_images(websocket))

        async for message in websocket:
            try:
                data = json.loads(message)
                logger.debug(f"Received message: {data}")
                if "command" in data:
                    await handle_command(data["command"], data.get("parameters"))
                else:
                    logger.warning("Invalid message format")
            except json.JSONDecodeError as e:
                logger.error(f"JSON decode error: {e}")
            except Exception as e:
                logger.exception(f"Error handling command: {e}")
    except websockets.exceptions.ConnectionClosedOK:
        logger.info("WebSocket connection closed")
    except Exception as e:
        logger.exception(f"WebSocket error: {e}")
    finally:
        image_task.cancel()
        try:
            await image_task
        except asyncio.CancelledError:
            pass

async def start_websocket_server():
    server = await websockets.serve(websocket_handler, "0.0.0.0", WEBSOCKET_PORT)
    logger.info(f"WebSocket server started (port: {WEBSOCKET_PORT})")
    await server.wait_closed()

# --- 이미지 전송 함수 ---
async def send_images(websocket):
    while True:
        try:
            image = camera.value
            if image is None:
              print("Camera image is None")
              await asyncio.sleep(0.1)
              continue

            image_data = bgr8_to_jpeg(image)
            image_base64 = base64.b64encode(image_data).decode('utf-8')
            await websocket.send(json.dumps({"image": image_base64}))
            await asyncio.sleep(0.1)  # 전송 간격 조절 (FPS)

        except websockets.exceptions.ConnectionClosedOK:
            logger.info("WebSocket connection closed (image send)")
            break
        except Exception as e:
            logger.exception(f"Error sending image: {e}")
            break

async def main():
    await start_websocket_server()

if __name__ == "__main__":
    asyncio.ensure_future(main())

DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Reseting PCA9685 MODE1 (without SLEEP) and MODE2
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFA
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFB
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFC
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFD
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x04 to register 0x01
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x01 to register 0x00
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Read 0x01 from register 0x00
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x01 to register 0x00
DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Setting PWM frequency to 1600 Hz
DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Estimated pre-scale: 2
DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Final pre-scale: 3
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Read 0x01 from register 0x00
DEBUG:Adafruit_I2

In [2]:
camera.stop()

In [1]:
# jetbot_control.py (JetBot - WebSocket Server + JetBot Control + Image Send)

import asyncio
import websockets
import json
import logging
from jetbot import Robot, Camera, bgr8_to_jpeg
import base64
import time
import random

# --- 로깅 ---
logging.basicConfig(level=logging.DEBUG)
logger = logging.getLogger(__name__)

# --- 설정 ---
WEBSOCKET_PORT = 8766
CAMERA_WIDTH = 300
CAMERA_HEIGHT = 300

# --- JetBot ---
robot = Robot()
camera = Camera.instance(width=CAMERA_WIDTH, height=CAMERA_HEIGHT)

# --- JetBot 명령 처리: 단순화된 동작 ---
async def handle_command(command: str, parameters: dict = None):
    logger.info(f"Handling JetBot command: {command}, Parameters: {parameters}")

    try:
        if command == "forward_fast":
            robot.forward(0.6)
            await asyncio.sleep(1)  # 비동기 sleep
            robot.stop()
        elif command == "forward_medium":
            robot.forward(0.4)
            await asyncio.sleep(1)
            robot.stop()
        elif command == "forward_slow":
            robot.forward(0.2)
            await asyncio.sleep(1)
            robot.stop()
        elif command == "backward_fast":
            robot.backward(0.6)
            await asyncio.sleep(1)
            robot.stop()
        elif command == "backward_medium":
            robot.backward(0.4)
            await asyncio.sleep(1)
            robot.stop()
        elif command == "backward_slow":
            robot.backward(0.2)
            await asyncio.sleep(1)
            robot.stop()
        elif command == "left_fast":
            robot.left(0.5)
            await asyncio.sleep(0.7)
            robot.stop()
        elif command == "left_medium":
            robot.left(0.3)
            await asyncio.sleep(0.7)
            robot.stop()
        elif command == "left_slow":
            robot.left(0.1)
            await asyncio.sleep(0.7)
            robot.stop()
        elif command == "right_fast":
            robot.right(0.5)
            await asyncio.sleep(0.7)
            robot.stop()
        elif command == "right_medium":
            robot.right(0.3)
            await asyncio.sleep(0.7)
            robot.stop()
        elif command == "right_slow":
            robot.right(0.1)
            await asyncio.sleep(0.7)
            robot.stop()
        elif command == "avoid_obstacle":
            direction = parameters.get("direction", "left") if parameters else "left"
            if direction == "left":
                await handle_command("left_medium")
            elif direction == "right":
                await handle_command("right_medium")
            await handle_command("forward_medium")
        elif command == "stop":
            robot.stop()
        elif command == "rotate":  # 각도 파라미터 삭제
            if parameters and "angle" in parameters: # angle 파라미터 삭제
                angle = parameters["angle"]
                if angle > 0: # angle 파라미터 삭제
                    await handle_command("right_medium") #90도 대신
                else:
                    await handle_command("left_medium") # -90도 대신
            else:
                logger.warning("Rotate command missing 'angle' parameter") # angle 파라미터 삭제

        elif command == "random_action":
            random_action = random.choice(list(BASIC_COMMANDS.keys()))
            await handle_command(random_action)

        elif command == "custom_command":
            if parameters and "prompt" in parameters:
                logger.info(f"Received Custom command prompt: {parameters['prompt']}")
            else:
                logger.warning("custom_command missing prompt")
        elif command == "none":
            pass
        else:
            logger.warning(f"Unknown command: {command}")

    except Exception as e:
        logger.exception(f"Error in handle_command: {e}")

# 미리 정의된 기본 명령
BASIC_COMMANDS = {
    "forward_fast": {"speed": 0.6, "duration": 1.0},
    "forward_medium": {"speed": 0.4, "duration": 1.0},
    "forward_slow": {"speed": 0.2, "duration": 1.0},
    "backward_fast": {"speed": 0.6, "duration": 1.0},
    "backward_medium": {"speed": 0.4, "duration": 1.0},
    "backward_slow": {"speed": 0.2, "duration": 1.0},
    "left_fast": {"speed": 0.5, "duration": 0.7},
    "left_medium": {"speed": 0.3, "duration": 0.7},
    "left_slow": {"speed": 0.1, "duration": 0.7},
    "right_fast": {"speed": 0.5, "duration": 0.7},
    "right_medium": {"speed": 0.3, "duration": 0.7},
    "right_slow": {"speed": 0.1, "duration": 0.7},
}

# --- 웹소켓 서버 ---
async def websocket_handler(websocket, path):
    logger.info(f"New WebSocket connection: {websocket.remote_address}")
    try:
        image_task = asyncio.ensure_future(send_images(websocket))

        async for message in websocket:
            try:
                data = json.loads(message)
                logger.debug(f"Received message: {data}")
                if "command" in data:
                    await handle_command(data["command"], data.get("parameters"))
                else:
                    logger.warning("Invalid message format")
            except json.JSONDecodeError as e:
                logger.error(f"JSON decode error: {e}")
            except Exception as e:
                logger.exception(f"Error handling command: {e}")
    except websockets.exceptions.ConnectionClosedOK:
        logger.info("WebSocket connection closed")
    except Exception as e:
        logger.exception(f"WebSocket error: {e}")
    finally:
        image_task.cancel()
        try:
            await image_task
        except asyncio.CancelledError:
            pass

async def start_websocket_server():
    server = await websockets.serve(websocket_handler, "0.0.0.0", WEBSOCKET_PORT)
    logger.info(f"WebSocket server started (port: {WEBSOCKET_PORT})")
    await server.wait_closed()

# --- 이미지 전송 함수 ---
async def send_images(websocket):
    while True:
        try:
            image = camera.value
            if image is None:
                logger.warning("Camera image is None")
                await asyncio.sleep(0.1)
                continue
            image_data = bgr8_to_jpeg(image)
            image_base64 = base64.b64encode(image_data).decode('utf-8')
            await websocket.send(json.dumps({"image": image_base64}))
            #await asyncio.sleep(0.1) # 이미지 전송 간격 주석처리
        except websockets.exceptions.ConnectionClosedOK:
            logger.info("WebSocket connection closed (image send)")
            break
        except Exception as e:
            logger.exception(f"Error sending image: {e}")
            break

async def main():
    await start_websocket_server()

if __name__ == "__main__":
    # Python 버전 확인 및 실행
    if sys.version_info >= (3, 7):  # Python 3.7 이상
        asyncio.run(main())
    else:  # Python 3.6 이하
        loop = asyncio.get_event_loop()
        try:
            loop.run_until_complete(main())
        except RuntimeError as e:
            if "Event loop is already running" not in str(e):
                raise
            else: # 이미 실행중
                logger.info("Event loop already running.  Continuing...")
        finally:
            try:
                loop.close() # 닫기
            except RuntimeError as e:
                if "Cannot close a running event loop" not in str(e):
                    raise
                else: # 이미 실행중
                    logger.info("Event loop already running.  Continuing...")

DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Reseting PCA9685 MODE1 (without SLEEP) and MODE2
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFA
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFB
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFC
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x00 to register 0xFD
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x04 to register 0x01
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x01 to register 0x00
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Read 0x01 from register 0x00
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Wrote 0x01 to register 0x00
DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Setting PWM frequency to 1600 Hz
DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Estimated pre-scale: 2
DEBUG:Adafruit_MotorHAT.Adafruit_PWM_Servo_Driver:Final pre-scale: 3
DEBUG:Adafruit_I2C.Device.Bus.1.Address.0X60:Read 0x01 from register 0x00
DEBUG:Adafruit_I2

RuntimeError: This event loop is already running

INFO:__main__:WebSocket server started (port: 8766)
DEBUG:websockets.protocol:server - state = CONNECTING
DEBUG:websockets.protocol:server - event = connection_made(<_SelectorSocketTransport fd=95 read=idle write=<idle, bufsize=0>>)
DEBUG:websockets.protocol:server - event = data_received(<516 bytes>)
DEBUG:websockets.server:server < GET / HTTP/1.1
DEBUG:websockets.server:server < Headers([('Host', '192.168.137.233:8766'), ('Connection', 'Upgrade'), ('Pragma', 'no-cache'), ('Cache-Control', 'no-cache'), ('User-Agent', 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/134.0.0.0 Safari/537.36 Edg/134.0.0.0'), ('Upgrade', 'websocket'), ('Origin', 'http://localhost:8000'), ('Sec-WebSocket-Version', '13'), ('Accept-Encoding', 'gzip, deflate'), ('Accept-Language', 'ko,en;q=0.9,en-US;q=0.8'), ('Sec-WebSocket-Key', 'tT06SiLPNiEp94pnrUnzjw=='), ('Sec-WebSocket-Extensions', 'permessage-deflate; client_max_window_bits')])
DEBUG:websockets.server:server > HTT